In [19]:
#Importar bibliotecas
import numpy as np
import torch
from torch.utils.data import Dataset, DataLoader, TensorDataset, random_split
print(torch.__version__)

1.7.1+cu110


In [2]:
#Configurar variáveis
dataset_input = "bin/dataset_input_consolidado.txt"
dataset_output = "bin/dataset_output_consolidado.txt"

In [3]:
#Inputando os dados
inputMatrix = np.loadtxt(dataset_input,dtype='float',delimiter=";")
outputMatrix = np.loadtxt(dataset_output,dtype='float',delimiter=";")#,usecols=np.arange(0,93))
#outputMatrix = np.array([(120, 5,120),
#                         (123,24,100),
#                         (154, 3,121)],dtype=float)
for i,c in enumerate(inputMatrix):
    print("{}Input Matrix={}Output Matrix".format(c,outputMatrix[i]))

[ 7.75796078e+06 -3.63653347e+05 -1.15200000e+00  5.79400000e+00
  7.75795507e+06 -3.63644516e+05 -8.39000000e-01  0.00000000e+00
  1.00000000e-03]Input Matrix=[0.    0.001 0.02 ]Output Matrix
[ 7.75796078e+06 -3.63653347e+05 -1.15200000e+00  5.78600000e+00
  7.75795507e+06 -3.63644515e+05 -8.39000000e-01  0.00000000e+00
 -8.00000000e-03]Input Matrix=[ 0.    -0.008  0.02 ]Output Matrix
[ 7.75796078e+06 -3.63653347e+05 -1.15200000e+00  5.77900000e+00
  7.75795508e+06 -3.63644514e+05 -8.38000000e-01  0.00000000e+00
 -1.80000000e-02]Input Matrix=[ 0.    -0.018  0.02 ]Output Matrix
[ 7.75796078e+06 -3.63653347e+05 -1.15200000e+00  5.77300000e+00
  7.75795508e+06 -3.63644515e+05 -8.38000000e-01  0.00000000e+00
 -2.90000000e-02]Input Matrix=[ 0.    -0.029  0.02 ]Output Matrix
[ 7.75796078e+06 -3.63653347e+05 -1.15200000e+00  5.76700000e+00
  7.75795508e+06 -3.63644515e+05 -8.38000000e-01  0.00000000e+00
 -3.80000000e-02]Input Matrix=[ 0.    -0.038  0.02 ]Output Matrix
[ 7.75796078e+06 -3.636

In [4]:
input_tensor = torch.from_numpy(inputMatrix)
output_tensor = torch.from_numpy(outputMatrix)

if torch.cuda.is_available():
    input_tensor = input_tensor.to("cuda")
    output_tensor = output_tensor.to("cuda")

In [23]:
#Preparando dataset (separando os dados em treino, teste e validação)

dataset = TensorDataset(input_tensor, output_tensor)
proportions = [.70, .20, .10]
lengths = [int(p * len(dataset)) for p in proportions]
lengths[-1] = len(dataset) - sum(lengths[:-1])
train_dataset, val_dataset, test_dataset = random_split(dataset, lengths)
print(len(dataset))
print(len(train_dataset))
print(len(val_dataset))
print(len(test_dataset))

21068
6019
3011
30098


In [24]:
train_loader = DataLoader(dataset=train_dataset, shuffle=True, batch_size=64, drop_last=True)
val_loader = DataLoader(dataset=val_dataset, shuffle=False, batch_size=64)
test_loader = DataLoader(dataset=test_dataset, shuffle=False, batch_size=64)

print("Length of the train_loader:", len(train_loader))
print("Length of the val_loader:", len(val_loader))
print("Length of the test_loader:", len(test_loader))

Length of the train_loader: 329
Length of the val_loader: 95
Length of the test_loader: 48


In [35]:
# Definindo o modelo

model = torch.nn.Sequential(
    torch.nn.Linear(9, 1200),
    torch.nn.ReLU(),
    torch.nn.Linear(1200, 600),
    torch.nn.ReLU(),
    torch.nn.Linear(600, 300),
    torch.nn.ReLU(),
    torch.nn.Linear(300, 150)    
)
model.to("cuda")
"""
model = torch.nn.Sequential(
    nn.Linear(8, 24),
    nn.ReLU(),
    nn.Linear(24, 12),
    nn.ReLU(),
    nn.Linear(12, 6),
    nn.ReLU(),
    nn.Linear(6, 1)
)
"""

'\nmodel = torch.nn.Sequential(\n    nn.Linear(8, 24),\n    nn.ReLU(),\n    nn.Linear(24, 12),\n    nn.ReLU(),\n    nn.Linear(12, 6),\n    nn.ReLU(),\n    nn.Linear(6, 1)\n)\n'

In [28]:
#Definindo os hiperparâmetros
learning_rate = 1e-3
batch_size = 64
epochs = 5

In [30]:
#Função loss
loss_fn = torch.nn.MSELoss()

In [31]:
#Optimizador
optimizer = torch.optim.SGD(model.parameters(), lr=learning_rate)

In [36]:
def train_loop(dataloader, model, loss_fn, optimizer):
    size = len(dataloader.dataset)
    # Set the model to training mode - important for batch normalization and dropout layers
    # Unnecessary in this situation but added for best practices
    model.train()
    for batch, (X, y) in enumerate(dataloader):
        # Compute prediction and loss
        pred = model(X)
        loss = loss_fn(pred, y)

        # Backpropagation
        loss.backward()
        optimizer.step()
        optimizer.zero_grad()

        if batch % 100 == 0:
            loss, current = loss.item(), (batch + 1) * len(X)
            print(f"loss: {loss:>7f}  [{current:>5d}/{size:>5d}]")


def test_loop(dataloader, model, loss_fn):
    # Set the model to evaluation mode - important for batch normalization and dropout layers
    # Unnecessary in this situation but added for best practices
    model.eval()
    size = len(dataloader.dataset)
    num_batches = len(dataloader)
    test_loss, correct = 0, 0

    # Evaluating the model with torch.no_grad() ensures that no gradients are computed during test mode
    # also serves to reduce unnecessary gradient computations and memory usage for tensors with requires_grad=True
    with torch.no_grad():
        for X, y in dataloader:
            pred = model(X)
            test_loss += loss_fn(pred, y).item()
            correct += (pred.argmax(1) == y).type(torch.float).sum().item()

    test_loss /= num_batches
    correct /= size
    print(f"Test Error: \n Accuracy: {(100*correct):>0.1f}%, Avg loss: {test_loss:>8f} \n")

In [37]:
for t in range(epochs):
    print(f"Epoch {t+1}\n-------------------------------")
    train_loop(train_loader, model, loss_fn, optimizer)
    test_loop(test_loader, model, loss_fn)
print("Done!")

Epoch 1
-------------------------------


RuntimeError: expected scalar type Float but found Double

In [ ]:
#Criando o modelo 
l0 = tf.keras.layers.Dense(units = 9, input_shape = [9])
l1 = tf.keras.layers.Dense(units = 64)
l2 = tf.keras.layers.Dense(units = 64)
#l3 = tf.keras.layers.Dense(units = 93)
l3 = tf.keras.layers.Dense(units = 3)

"""Modelo inicial: 
l0 = tf.keras.layers.Dense(units = 4, input_shape = [4])
l1 = tf.keras.layers.Dense(units = 64)
l2 = tf.keras.layers.Dense(units = 128)
l3 = tf.keras.layers.Dense(units = 3) """

model = tf.keras.Sequential([l0,l1,l2,l3])

In [ ]:
#Compilando o modelo
model.compile(loss='mean_squared_error', optimizer=optimizers.RMSprop(lr=1e-4))#tf.keras.optimizers.Adam(0.1)), loss='mean_squared_error'

In [ ]:
#Treinar o modelo
history = model.fit(inputMatrix,outputMatrix,epochs=500,verbose=False)#epochs inicial=500
print("Finished training the model!")